## Import Libraries and Data

In [6]:
# Import Libraries
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib
import folium 
from folium.plugins import FastMarkerCluster
import os

In [8]:
# Path
path = r'/Users/michele/Desktop/CF/files/Module6/AirBnb'

In [10]:
# Import files
listing = pd.read_pickle(os.path.join(path, 'Data', 'Prepared', 'list_concat.pkl'))

In [12]:
l_rent = pd.read_pickle(os.path.join(path, 'Data', 'Prepared', 'long_rental.pkl'))

In [14]:
s_rent = pd.read_pickle(os.path.join(path, 'Data', 'Prepared', 'short_rental.pkl'))

In [16]:
# Import GeoJson file
geo = r'/Users/michele/Desktop/CF/files/Module6/AirBnb/Data/Original/bezirks.geojson'

## Geo Analysis

#### Distribution of the listings in the city

In [18]:
# Main map
m = folium.Map(location=[listing['latitude'].iloc[0], listing['longitude'].iloc[0]], zoom_start=10, tiles='CartoDB positron')
# Add the GeoJson layer (outline or region borders)
folium.GeoJson(
    geo,  
    name='GeoJson Region',
    style_function=lambda x: {
        'fillColor': 'none',  
        'color': 'grey',  
        'weight': 1  
    }
).add_to(m)
# Create a feature group for the full dataset 
full_layer = folium.FeatureGroup(name="All Listings")
locations = listing[['latitude', 'longitude']].values.tolist() 
FastMarkerCluster(locations).add_to(full_layer)
full_layer.add_to(m)
# Create a feature group for long rental 
subset1 = l_rent
locations1 = l_rent[['latitude', 'longitude']].values.tolist()
subset1_layer = folium.FeatureGroup(name="Long Rental")
FastMarkerCluster(locations1).add_to(subset1_layer)
subset1_layer.add_to(m)
# Create a feature group for short rental 
subset2 = s_rent
locations2 = s_rent[['latitude', 'longitude']].values.tolist()
subset2_layer = folium.FeatureGroup(name="Short Rental")
FastMarkerCluster(locations2).add_to(subset2_layer)
subset2_layer.add_to(m)
# Add Layer control to toggle between them
folium.LayerControl().add_to(m)
# Show map
m

#### Average monthly price for long term listings

In [20]:
# Calculate monthly price for visualisation
l_rent['monthly_price'] = l_rent['price'] * 30

In [22]:
# Change data type
l_rent['monthly_price'] = l_rent['monthly_price'].astype(int)

In [24]:
# Calculate the median monthly price
mth_price = l_rent.groupby('neighbourhood').agg({'monthly_price':'median'}).reset_index()

In [26]:
# Add columns names
mth_price.columns = ['neighbourhood', 'monthly_price']

In [28]:
# Choropleth Map of the median price per neighbourhood
m = folium.Map(location=[52.520008, 13.404954], zoom_start=10, tiles='CartoDB positron')
# Choropleth map
folium.Choropleth(
    geo_data=geo,
    data=mth_price,
    columns=['neighbourhood', 'monthly_price'],
    key_on='feature.properties.Gemeinde_name',
    fill_color='YlGnBu', 
    fill_opacity=0.6, 
    line_opacity=0.1,
    legend_name='Average Monthly Price'
    ).add_to(m)
# Add layer control
folium.LayerControl().add_to(m)
# Show map
m 